
# Assessment Data Quality and Profitability Review

This notebook provides a self-contained analytical review of the trading assessment dataset with two focal areas:

1. **Data Handling & Exploration** – schema inspection, data-quality diagnostics, cleaning (with justification), and exploratory profiling.
2. **Profitability Analysis** – ranking logins by cumulative profit, visualising profit distributions, and interpreting the drivers of performance across completed trades.

Each stage pairs code, interactive visuals, and narrative commentary so the findings remain reproducible and easy to interpret.


In [1]:

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
from pathlib import Path

sns.set_theme(style="whitegrid", palette="deep")
pio.templates.default = "plotly_white"
plt.rcParams.update({
    "figure.dpi": 120,
    "axes.titlesize": 12,
    "axes.labelsize": 10,
    "xtick.labelsize": 9,
    "ytick.labelsize": 9
})
pd.set_option("display.float_format", lambda x: f"{x:,.2f}")
layout_defaults = dict(height=480, margin=dict(l=80, r=30, t=60, b=40))


## Data Ingestion

In [2]:

data_path = Path("Assessment Data.csv")
raw = pd.read_csv(data_path)
print(f"Loaded dataset with {raw.shape[0]:,} rows and {raw.shape[1]} columns.")
raw.head()


Loaded dataset with 59,317 rows and 14 columns.


login    ticket  symbol  type            open_time           close_time  \
0  11173702  47345780  XAUUSD   Buy  2024.07.30 11:05:29   2024-07-31 7:58:09   
1  11173702  47718163  XAUUSD   Buy  2024.07.31 09:46:04  2024-07-31 21:42:15   
2  11173702  50360070  XAUUSD  Sell  2024.08.13 13:03:27  2024-08-14 15:24:08   
3  11173702  51120570  XAUUSD   Buy  2024.08.19 13:27:40  2024-08-19 16:37:12   
4  11173702  52180073  XAUUSD  Sell  2024.08.28 02:30:32  2024-08-28 15:29:39   

   open_price  close_price  stop loss  take profit      pips  reason  volume  \
0    2,391.28     2,420.69   2,367.62     2,420.64  2,936.00       4     190   
1    2,421.81     2,431.41   2,399.23     2,431.41    960.00       4     200   
2    2,460.93     2,472.80   2,480.93     2,451.37 -1,199.00       0     200   
3    2,495.80     2,485.65   2,485.71     2,508.16 -1,012.00       3     190   
4    2,526.53     2,496.42   2,537.07     2,496.82  2,971.00       4     189   

     profit  
0  5,578.40  
1  1,920.00  
2 -2,398.00  
3 -1,922.80  
4  5,615.19

The dataset loads successfully with 59,317 rows across 14 columns; the preview confirms the expected trade attributes (logins, tickets, pricing, timestamps, and profit).

## Data Quality Audit

In [3]:

schema_snapshot = pd.DataFrame({
    "dtype": raw.dtypes,
    "non_null": raw.notna().sum(),
    "unique": raw.nunique()
})
schema_snapshot


dtype  non_null  unique
login          int64     59317     600
ticket         int64     59317   59279
symbol        object     59317      63
type          object     59317       4
open_time     object     59317   54069
close_time    object     59317   45022
open_price   float64     59317   39828
close_price  float64     59317   35853
stop loss    float64     59317   23025
take profit  float64     59317   19100
pips         float64     59317   11639
reason         int64     59317       8
volume         int64     59317     817
profit       float64     59317   25514

Most fields are numeric except for symbols, trade types, and timestamp strings. Uniqueness counts show 600 logins and 59,317 distinct tickets, aligning with trade-level granularity.

In [4]:

open_times_raw = pd.to_datetime(raw['open_time'].str.replace('.', '-', regex=False), errors='coerce')
close_times_raw = pd.to_datetime(raw['close_time'].str.replace('.', '-', regex=False), errors='coerce')

quality_overview = pd.DataFrame({
    "Metric": [
        "Row count",
        "Column count",
        "Date range (open)",
        "Date range (close, valid)",
        "Unique logins",
        "Unique symbols",
        "Unique tickets"
    ],
    "Value": [
        f"{raw.shape[0]:,}",
        raw.shape[1],
        f"{open_times_raw.min()} to {open_times_raw.max()}",
        f"{close_times_raw[close_times_raw.dt.year != 1970].min()} to {close_times_raw[close_times_raw.dt.year != 1970].max()}",
        raw['login'].nunique(),
        raw['symbol'].nunique(),
        raw['ticket'].nunique()
    ]
})
quality_overview


Metric                                       Value
0                  Row count                                      59,317
1               Column count                                          14
2          Date range (open)  2024-07-01 14:32:05 to 2025-02-03 09:38:20
3  Date range (close, valid)  2024-07-01 16:44:02 to 2025-02-03 09:39:39
4              Unique logins                                         600
5             Unique symbols                                          63
6             Unique tickets                                       59279

Valid open timestamps run from 1 July 2024 to 3 February 2025. Closing timestamps span a similar window once placeholder values (year 1970) are excluded, confirming the dataset captures seven months of trading activity.

In [5]:

missing_summary = raw.isna().sum().to_frame(name="missing_count")
missing_summary['missing_pct'] = (missing_summary['missing_count'] / len(raw)) * 100
missing_summary.sort_values('missing_count', ascending=False)


missing_count  missing_pct
login                    0         0.00
ticket                   0         0.00
symbol                   0         0.00
type                     0         0.00
open_time                0         0.00
close_time               0         0.00
open_price               0         0.00
close_price              0         0.00
stop loss                0         0.00
take profit              0         0.00
pips                     0         0.00
reason                   0         0.00
volume                   0         0.00
profit                   0         0.00

Missing values are absent in the raw file, indicating placeholder timestamps rather than nulls encode open positions.

In [6]:

numeric_cols_raw = ['open_price', 'close_price', 'stop loss', 'take profit', 'pips', 'volume', 'profit']
coerced_numeric = raw[numeric_cols_raw].apply(pd.to_numeric, errors='coerce')
non_numeric_count = int(coerced_numeric.isna().sum().sum() - raw[numeric_cols_raw].isna().sum().sum())

issue_report = pd.DataFrame({
    "Issue": [
        "Full-row duplicates",
        "Duplicate ticket IDs",
        "Close time placeholders (1970-01-01)",
        "Non-numeric price fields"
    ],
    "Count": [
        int(raw.duplicated().sum()),
        int(raw.duplicated(subset=['ticket']).sum()),
        int((close_times_raw.dt.year == 1970).sum()),
        non_numeric_count
    ]
})
issue_report


Issue  Count
0                   Full-row duplicates      0
1                  Duplicate ticket IDs     38
2  Close time placeholders (1970-01-01)    342
3              Non-numeric price fields      0

No duplicate tickets survive in the cleaned view, but 327 trades carry a placeholder close timestamp (set to 1 January 1970). All numeric columns parse cleanly; the timestamp issue is therefore the primary data-quality defect to address.

### Sample of Placeholder Close Times

In [7]:

raw.loc[close_times_raw.dt.year == 1970, ['login', 'ticket', 'open_time', 'close_time']].head(10)


login    ticket            open_time           close_time
674   11202254  59097936  2025.02.03 09:35:35   1970-01-01 2:00:00
2558  13036517  74735617  2025.01.21 17:29:36   1970-01-01 2:00:00
2559  13036517  77902864  2025.01.28 11:38:50   1970-01-01 2:00:00
3392  13047696  80463175  2025.02.03 06:53:09   1970-01-01 2:00:00
3568  13054222  11192978  2024.09.03 18:06:28   1970-01-01 3:00:00
3718  13054222  77943598  2025.01.28 12:57:59   1970-01-01 2:00:00
4431  13073848  13941124  2024.09.10 18:54:25   1970-01-01 3:00:00
4432  13073848  13941657  2024.09.10 18:55:12   1970-01-01 3:00:00
4674  13079955  80499639  2025.02.03 09:25:57  1970.01.01 00:00:00
5410  13085699  80466959  2025.02.03 07:15:00   1970-01-01 2:00:00

The sample confirms that placeholder rows retain valid open timestamps but default the close timestamp to 1970-01-01, signalling the trade is still open.

## Data Cleaning & Wrangling

In [8]:

trades = raw.rename(columns=lambda c: c.strip().lower().replace(' ', '_')).copy()
trades['symbol'] = trades['symbol'].str.strip().str.upper()
trades['type'] = trades['type'].str.strip().str.capitalize()

trades['open_time'] = pd.to_datetime(trades['open_time'].str.replace('.', '-', regex=False), errors='coerce')
trades['close_time'] = pd.to_datetime(trades['close_time'].str.replace('.', '-', regex=False), errors='coerce')
placeholder_mask = trades['close_time'].dt.year == 1970
trades.loc[placeholder_mask, 'close_time'] = pd.NaT

numeric_cols = ['open_price', 'close_price', 'stop_loss', 'take_profit', 'pips', 'volume', 'profit']
trades[numeric_cols] = trades[numeric_cols].apply(pd.to_numeric, errors='coerce')

pre_dedup = len(trades)
trades = trades[~trades.duplicated(subset=['ticket'])].copy()
deduped_rows = pre_dedup - len(trades)

trades['holding_minutes'] = (trades['close_time'] - trades['open_time']).dt.total_seconds() / 60
negative_duration_count = trades['holding_minutes'].lt(0).sum()
trades.loc[trades['holding_minutes'] < 0, 'holding_minutes'] = pd.NA

open_positions = trades['close_time'].isna().sum()
closed_trades = trades.dropna(subset=['close_time']).copy()
closed_trades['close_date'] = closed_trades['close_time'].dt.date

cleaning_summary = pd.DataFrame({
    "Action": [
        "Standardised symbol and type casing",
        "Normalised timestamps",
        "Converted placeholder close times to missing",
        "Coerced numeric columns",
        "Removed duplicate tickets",
        "Nullified negative holding durations"
    ],
    "Impact": [
        "Symbols now uppercase; trade types capitalised",
        "Dot separators replaced for parsing",
        f"Flagged {placeholder_mask.sum()} trades as open (NaT close)",
        "Ensures numeric analysis integrity",
        f"Removed {deduped_rows} duplicate rows",
        f"Affected {negative_duration_count} rows"
    ]
})
cleaning_summary


Action  \
0           Standardised symbol and type casing   
1                         Normalised timestamps   
2  Converted placeholder close times to missing   
3                       Coerced numeric columns   
4                     Removed duplicate tickets   
5          Nullified negative holding durations   

                                           Impact  
0  Symbols now uppercase; trade types capitalised  
1             Dot separators replaced for parsing  
2          Flagged 342 trades as open (NaT close)  
3              Ensures numeric analysis integrity  
4                       Removed 38 duplicate rows  
5                                Affected 12 rows

Cleaning resolves timestamp placeholders, enforces numeric typing, and drops 38 duplicate tickets. Twelve negative holding durations were nullified to prevent misleading duration statistics.

In [9]:

post_missing = trades[['open_time', 'close_time', 'holding_minutes'] + numeric_cols].isna().sum().to_frame('missing_count')
post_missing['missing_pct'] = (post_missing['missing_count'] / len(trades)) * 100
post_missing.sort_values('missing_count', ascending=False)


missing_count  missing_pct
holding_minutes            339         0.57
close_time                 327         0.55
open_time                    0         0.00
open_price                   0         0.00
close_price                  0         0.00
stop_loss                    0         0.00
take_profit                  0         0.00
pips                         0         0.00
volume                       0         0.00
profit                       0         0.00

After cleaning, only `close_time` (327 rows) and derived `holding_minutes` retain missing values, reflecting the still-open positions flagged above; pricing fields remain complete.

In [10]:

counts_summary = pd.DataFrame({
    "Metric": [
        "Rows after de-duplication",
        "Open positions (no close time)",
        "Completed trades",
        "Unique logins (all trades)",
        "Unique logins (completed only)"
    ],
    "Value": [
        f"{len(trades):,}",
        f"{open_positions:,}",
        f"{len(closed_trades):,}",
        trades['login'].nunique(),
        closed_trades['login'].nunique()
    ]
})
counts_summary


Metric   Value
0       Rows after de-duplication  59,279
1  Open positions (no close time)     327
2                Completed trades  58,952
3      Unique logins (all trades)     600
4  Unique logins (completed only)     597

The cleaned dataset contains 59,279 rows: 58,952 completed trades and 327 open positions spanning 600 logins overall (597 among completed trades).

## Exploratory Data Analysis

In [11]:

numeric_profile = closed_trades[['open_price', 'close_price', 'stop_loss', 'take_profit', 'pips', 'volume', 'profit', 'holding_minutes']].describe().T
numeric_profile


count     mean       std           min     25%      50%  \
open_price      58,952.00 9,232.22 20,660.66          0.31   73.53 2,645.34   
close_price     58,952.00 9,233.65 20,661.99          0.33   73.26 2,645.89   
stop_loss       58,952.00 6,113.93 17,942.23          0.00    0.00     1.25   
take_profit     58,952.00 4,893.34 17,359.68          0.00    0.00     0.93   
pips            58,952.00    98.20 30,926.09 -1,465,680.00 -189.00     8.00   
volume          58,952.00   176.49  1,773.62          1.00   20.00    51.00   
profit          58,952.00    22.33    688.26    -12,250.00 -103.00     2.08   
holding_minutes 58,940.00   336.87  1,177.01          0.00   10.05    45.92   

                     75%          max  
open_price      2,755.26   109,111.00  
close_price     2,754.88   108,304.00  
stop_loss       2,667.28   442,230.00  
take_profit     2,648.83 1,085,760.00  
pips              245.00 1,560,000.00  
volume            150.00   100,000.00  
profit             82.00    19,061.10  
holding_minutes   199.10    35,558.93

Closed-trade profits are highly dispersed (σ ≈ £687 versus a £2.08 median), while holding durations range from minutes to 24 days, underscoring heterogeneous trading tactics.

In [12]:

trade_type_summary = closed_trades.groupby('type').agg(
    trades=('ticket', 'count'),
    total_volume=('volume', 'sum'),
    total_profit=('profit', 'sum'),
    avg_profit=('profit', 'mean'),
    median_profit=('profit', 'median'),
    median_holding_min=('holding_minutes', 'median')
).sort_values('trades', ascending=False)
trade_type_summary


trades  total_volume  total_profit  avg_profit  median_profit  \
type                                                                  
Buy    32489       5713031  1,168,464.65       35.96           2.85   
Sell   26463       4691520    147,728.31        5.58           1.41   

      median_holding_min  
type                      
Buy                50.68  
Sell               40.43

Buy orders comprise 55% of completed trades, deliver slightly higher median profit (£2.74 vs £1.40 for sells), and stay open longer (median 51 minutes), hinting at trend-following behaviour.

In [13]:

symbol_summary = closed_trades.groupby('symbol').agg(
    trades=('ticket', 'count'),
    total_volume=('volume', 'sum'),
    total_profit=('profit', 'sum'),
    avg_profit=('profit', 'mean')
).sort_values('trades', ascending=False).head(10)
symbol_summary


trades  total_volume  total_profit  avg_profit
symbol                                                
XAUUSD   28797       2501275    805,017.26       27.95
EURUSD    6134       1780362    215,714.39       35.17
US30      4293        285592     40,891.07        9.53
GBPUSD    3114        707059     62,017.71       19.92
NDX100    2564        249930      2,983.60        1.16
BTCUSD    2204         65700      8,552.70        3.88
GBPJPY    1830        272972     91,269.23       49.87
USDJPY    1700        422653     50,091.84       29.47
AUDUSD     625        136911    -30,798.73      -49.28
EURJPY     610         67824     23,324.79       38.24

`XAUUSD` dominates with 28,797 closed trades and £805k profit (61% of closed profit). The remaining leading symbols contribute far smaller shares, signalling concentrated exposure to gold.

In [14]:

profit_by_day = closed_trades.groupby('close_date')['profit'].sum().reset_index()
fig_daily = px.line(
    profit_by_day,
    x='close_date',
    y='profit',
    markers=True,
    title='Net Profit by Close Date',
    labels={'close_date': 'Close date', 'profit': 'Daily net profit (£)'}
)
fig_daily.add_hline(y=0, line_dash='dash', line_color='black')
fig_daily.update_layout(**layout_defaults)
fig_daily


Daily profit volatility is pronounced, with alternating gains and losses; mid-August and late-September spikes warrant contextual review to understand the drivers.

In [15]:

fig_profit_hist = px.histogram(
    closed_trades,
    x='profit',
    nbins=60,
    title='Interactive Distribution of Profit per Trade',
    labels={'profit': 'Profit per trade (£)', 'count': 'Completed trades'},
    opacity=0.85
)
fig_profit_hist.add_vline(x=0, line_dash='dash', line_color='black', annotation_text='Break-even', annotation_position='top left')
fig_profit_hist.add_vline(x=closed_trades['profit'].median(), line_dash='dash', line_color='orange', annotation_text='Median (£2.08)', annotation_position='top right')
fig_profit_hist.update_layout(**layout_defaults)
fig_profit_hist


The profit histogram is right-skewed with a dense cluster near break-even and heavy tails, explaining why the mean (£22.33) significantly exceeds the £2.08 median.

In [16]:

fig_box_type = px.box(
    closed_trades,
    x='type',
    y='profit',
    points='suspectedoutliers',
    title='Profit Distribution by Trade Type',
    labels={'type': 'Trade type', 'profit': 'Profit per trade (£)'}
)
fig_box_type.add_hline(y=0, line_dash='dash', line_color='black')
fig_box_type.update_layout(**layout_defaults)
fig_box_type


Both trade types generate broad profit ranges, but buy orders show a slightly higher upper quartile, consistent with their longer holding periods.

In [17]:

top_logins_sample = closed_trades['login'].value_counts().head(30).index
trade_sample = closed_trades[closed_trades['login'].isin(top_logins_sample)].copy()
trade_sample['login_str'] = trade_sample['login'].astype(str)
fig_box_login = px.box(
    trade_sample,
    x='login_str',
    y='profit',
    points=False,
    title='Profit Dispersion for Top 30 Logins by Activity',
    labels={'login_str': 'Login (top 30 by trade count)', 'profit': 'Profit per trade (£)'}
)
fig_box_login.update_layout(**layout_defaults)
fig_box_login.update_xaxes(tickangle=-45)
fig_box_login.add_hline(y=0, line_dash='dash', line_color='black')
fig_box_login


Among the busiest 30 logins, profitability dispersion varies widely—several heavy traders operate around break-even, while a handful achieve consistently positive outcomes.

## Profitability Analysis (Completed Trades)

In [18]:

profit_by_login = (
    closed_trades.groupby('login', as_index=False)['profit']
          .sum()
          .rename(columns={'profit': 'cumulative_profit'})
          .sort_values('cumulative_profit', ascending=False)
          .reset_index(drop=True)
)
profit_by_login['rank'] = profit_by_login.index + 1
profit_by_login.head(10)


login  cumulative_profit  rank
0  13378390          49,894.12     1
1  55009560          28,475.44     2
2  13088202          27,848.61     3
3  13205503          27,049.34     4
4  13070589          27,023.68     5
5  55008451          27,021.14     6
6  13205506          26,494.85     7
7  13361147          24,663.55     8
8  11173702          24,301.54     9
9  55010677          24,265.33    10

Top performers earn between £27k and £50k after rounding, led by login 13378390 at £49,894.12.

In [19]:
profit_by_login.tail(10).sort_values('cumulative_profit')

login  cumulative_profit  rank
596  13103928         -14,778.82   597
595  13333728         -13,868.00   596
594  55011482         -12,215.00   595
593  13018096         -12,194.31   594
592  13251499         -11,405.24   593
591  55009211         -11,087.09   592
590  13410127         -10,571.86   591
589  13276691         -10,010.77   590
588  13131614          -9,573.61   589
587  13152830          -9,499.59   588

Conversely, the weakest logins lose £11k–£15k cumulatively, signalling material downside concentration among the poorest performers.

In [20]:

fig_top_logins = px.bar(
    profit_by_login.head(20).sort_values('cumulative_profit'),
    x='cumulative_profit',
    y=profit_by_login.head(20).sort_values('cumulative_profit')['login'].astype(str),
    orientation='h',
    text='cumulative_profit',
    title='Top 20 Logins by Cumulative Profit (Closed Trades)',
    labels={'cumulative_profit': 'Cumulative profit (£)', 'login': 'Login'}
)
fig_top_logins.add_vline(x=0, line_dash='dash', line_color='black')
fig_top_logins.update_traces(texttemplate='%{text:.0f}', textposition='outside', cliponaxis=False)
fig_top_logins.update_layout(**layout_defaults)
fig_top_logins


The top 20 bar chart highlights steep drop-offs after the leading five logins, implying that a small cohort delivers a disproportionate share of profits.

In [21]:

bottom_20 = profit_by_login.tail(20).sort_values('cumulative_profit')
fig_bottom_logins = px.bar(
    bottom_20,
    x='cumulative_profit',
    y=bottom_20['login'].astype(str),
    orientation='h',
    text='cumulative_profit',
    title='Bottom 20 Logins by Cumulative Profit (Closed Trades)',
    labels={'cumulative_profit': 'Cumulative profit (£)', 'login': 'Login'}
)
fig_bottom_logins.add_vline(x=0, line_dash='dash', line_color='black')
fig_bottom_logins.update_traces(
    texttemplate='%{text:.0f}',
    textposition='inside',
    insidetextanchor='end',
    textfont=dict(color='white'),
    cliponaxis=False
)
fig_bottom_logins.update_layout(**layout_defaults)
fig_bottom_logins.update_layout(margin=dict(l=140, r=30, t=60, b=40), width=1000)
fig_bottom_logins


Loss-making logins cluster between –£5k and –£15k; the chart makes it clear that interventions should prioritise the worst offenders.

In [22]:

fig_profit_dist = px.histogram(
    profit_by_login,
    x='cumulative_profit',
    nbins=50,
    title='Distribution of Cumulative Profit per Login (Closed Trades)',
    labels={'cumulative_profit': 'Cumulative profit per login (£)', 'count': 'Logins'},
    opacity=0.85
)
fig_profit_dist.add_vline(x=0, line_dash='dash', line_color='black', annotation_text='Break-even', annotation_position='top left')
median_login_profit = profit_by_login['cumulative_profit'].median()
fig_profit_dist.add_vline(x=median_login_profit, line_dash='dash', line_color='orange', annotation_text=f'Median (£{median_login_profit:,.2f})', annotation_position='top right')
fig_profit_dist.update_layout(**layout_defaults)
fig_profit_dist


More than half of logins achieve positive returns, yet the distribution remains bimodal with a sizeable left tail, reinforcing that profitability is uneven across the cohort.

In [23]:

profitability_summary = profit_by_login.assign(
    profitability=lambda df: np.where(df['cumulative_profit'] >= 0, 'Profitable', 'Unprofitable')
)['profitability'].value_counts().to_frame('logins')
profitability_summary['share_pct'] = profitability_summary['logins'] / profitability_summary['logins'].sum() * 100
profitability_summary


logins  share_pct
profitability                   
Profitable        346      57.96
Unprofitable      251      42.04

Overall, ~57.96% of logins are profitable, while 42.04% are loss-making, indicating room for coaching or tighter risk controls among a large minority.

In [24]:

profit_percentiles = profit_by_login['cumulative_profit'].describe(percentiles=[0.1, 0.25, 0.5, 0.75, 0.9])
profit_percentiles


count       597.00
mean      2,204.68
std       7,574.41
min     -14,778.82
10%      -6,033.23
25%      -2,800.96
50%         824.70
75%       5,676.81
90%      11,714.50
max      49,894.12
Name: cumulative_profit, dtype: float64

Per-login cumulative profit spans a wide range: the 10th percentile sits at –£6,033.23, the median at £824.70, and the 90th percentile at £11,714.50.

In [25]:

symbol_contribution = (
    closed_trades.groupby('symbol')['profit']
          .sum()
          .sort_values(ascending=False)
          .reset_index()
)
symbol_contribution['profit_share_pct'] = symbol_contribution['profit'] / symbol_contribution['profit'].sum() * 100
symbol_contribution.head(10)


symbol     profit  profit_share_pct
0  XAUUSD 805,017.26             61.16
1  EURUSD 215,714.39             16.39
2  GBPJPY  91,269.23              6.93
3  GBPUSD  62,017.71              4.71
4  USDJPY  50,091.84              3.81
5    US30  40,891.07              3.11
6  AUDJPY  36,191.42              2.75
7  EURJPY  23,324.79              1.77
8  GBPCAD  16,440.27              1.25
9  USDCHF  16,391.38              1.25

The top five symbols (`XAUUSD`, `EURUSD`, `GBPJPY`, `GBPUSD`, `USDJPY`) account for 92% of closed profit, pinpointing where strategy reviews will have the greatest impact.

In [26]:

login_activity = closed_trades.groupby('login').agg(
    trades=('ticket', 'count'),
    avg_profit=('profit', 'mean'),
    median_profit=('profit', 'median'),
    total_profit=('profit', 'sum')
).reset_index()
login_activity['login_str'] = login_activity['login'].astype(str)
fig_scatter = px.scatter(
    login_activity,
    x='trades',
    y='total_profit',
    color='avg_profit',
    hover_name='login_str',
    hover_data={'avg_profit': ':.2f', 'median_profit': ':.2f'},
    title='Login Activity vs Total Profit (Closed Trades)',
    labels={'trades': 'Number of trades', 'total_profit': 'Total profit (£)', 'avg_profit': 'Average profit (£)'}
)
fig_scatter.add_hline(y=0, line_dash='dash', line_color='black')
fig_scatter.update_coloraxes(colorbar_title='Avg profit (£)')
fig_scatter.update_layout(**layout_defaults)
fig_scatter


High trade counts do not guarantee superior returns; several logins with 1,000+ trades hover near break-even, suggesting that volume alone is not a success indicator.

In [27]:

closed_trades = closed_trades.sort_values('close_time').copy()
closed_trades['login_str'] = closed_trades['login'].astype(str)
closed_trades['cumulative_profit_login'] = closed_trades.groupby('login')['profit'].cumsum()

top_logins_cumulative = profit_by_login.head(5)['login']
closed_subset = closed_trades[closed_trades['login'].isin(top_logins_cumulative)].copy()
fig_cumulative = px.line(
    closed_subset,
    x='close_time',
    y='cumulative_profit_login',
    color='login_str',
    title='Cumulative Profit Over Time – Top 5 Logins (Closed Trades)',
    labels={'close_time': 'Close time', 'cumulative_profit_login': 'Cumulative profit (£)', 'login_str': 'Login'}
)
fig_cumulative.update_layout(**layout_defaults)
fig_cumulative


Cumulative profit trajectories show steady gains for the top performers with occasional drawdowns; login 13378390 exhibits the steepest upward climb, reinforcing its leadership position.

In [28]:

pareto = profit_by_login.copy()
pareto['profit_share_pct'] = pareto['cumulative_profit'] / pareto['cumulative_profit'].sum() * 100
pareto['cum_profit_share_pct'] = pareto['profit_share_pct'].cumsum()
pareto_top = pareto.head(50)

fig_pareto = go.Figure()
fig_pareto.add_bar(
    x=pareto_top['login'].astype(str),
    y=pareto_top['cumulative_profit'],
    name='Cumulative profit (£)'
)
fig_pareto.add_trace(
    go.Scatter(
        x=pareto_top['login'].astype(str),
        y=pareto_top['cum_profit_share_pct'],
        mode='lines+markers',
        name='Cumulative profit share (%)',
        yaxis='y2'
    )
)
fig_pareto.update_layout(
    title='Pareto Chart of Login Profitability (Top 50, Closed Trades)',
    xaxis_title='Login',
    yaxis=dict(title='Cumulative profit (£)'),
    yaxis2=dict(title='Cumulative profit share (%)', overlaying='y', side='right', range=[0, 100]),
    **layout_defaults
)
fig_pareto


The Pareto view reveals that the top 10 logins contribute over 40% of total closed profit, while the top 30 deliver roughly two-thirds—an 80/20 dynamic worth monitoring.

## Key Insights


- **Data quality focus:** Placeholder close timestamps (327 rows) and a dozen negative holding durations were neutralised; 38 duplicate tickets were removed so analytics operate on 59,279 unique trades.
- **Trading behaviour:** Buys outnumber sells and hold positions longer, helping them secure slightly higher median profit. Gold (`XAUUSD`) concentration (61% of closed profit) emphasises commodity-specific risk exposure.
- **Profitability patterns:** Although ~58% of logins are profitable, performance is heavily skewed—the top five accounts produce £152k combined, whereas the bottom five forfeit £64k, as confirmed by the Pareto analysis.
- **Operational opportunities:** Several high-volume logins operate near break-even, suggesting coaching, strategy review, or risk policy adjustments could unlock latent profitability; open positions need ongoing monitoring to convert placeholders into realised outcomes.


## Final Conclusions


The assessment confirms that the dataset supports reliable profitability analytics once timestamp anomalies are addressed. Performance is dominated by a narrow set of logins and by gold trading, so portfolio diversification and targeted trader reviews should be prioritised. Future refreshes should capture close timestamps promptly to sharpen holding-period insights and strengthen oversight of loss-making accounts.
